# 2. Data Wrangling

## 2.1. Installing Libraries

In [1]:
import numpy as np
import pandas as pd

import pandas_profiling

import requests

import collections

import datetime as datetime

import re

from library.sb_utils import save_file


## 2.2. Importing Data

In [2]:
users=pd.read_csv('../raw_data/Dataset.csv')

In [3]:
movie_id=pd.read_csv('../raw_data/Movie_Id_Titles.csv')

In [4]:
credits=pd.read_csv('../raw_data/credits.csv')

In [5]:
keywords=pd.read_csv('../raw_data/keywords.csv')

In [6]:
links=pd.read_csv('../raw_data/links.csv')

In [7]:
links_small=pd.read_csv('../raw_data/links_small.csv')

In [64]:
movies_metadata=pd.read_csv('../raw_data/movies_metadata.csv')

C:\Users\User\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3071: DtypeWarning: Columns (10) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [9]:
ratings=pd.read_csv('../raw_data/ratings.csv')

## 2.3. User Data

### 2.3.1 User Data Dictionary

In [10]:
users.head()

user_id  item_id  rating  timestamp
0        0       50       5  881250949
1        0      172       5  881250949
2        0      133       1  881250949
3      196      242       3  881250949
4      186      302       3  891717742

In [11]:
users.shape

(100003, 4)

In [12]:
report = users.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report

### 2.3.2 Cleaning User Data

#### 2.3.2.1 Checking for Data Type Constraints

In [13]:
users.dtypes

user_id      int64
item_id      int64
rating       int64
timestamp    int64
dtype: object

In [14]:
users['user_id']=users['user_id'].astype(str)
users['item_id']=users['item_id'].astype(str)

users.dtypes

user_id      object
item_id      object
rating        int64
timestamp     int64
dtype: object

#### 2.3.2.2 Checking for duplicates

In [15]:
users.duplicated(subset=['user_id'], keep='first').value_counts()

True     99059
False      944
dtype: int64

Duplicated user_id means that a user rated more than one movie. Therefore, 944 users only rated one movie in the sample.

#### 2.3.2.3 Checking for missing values

In [16]:
users.isna().any()

user_id      False
item_id      False
rating       False
timestamp    False
dtype: bool

There are no missing values

### 2.3.3 Saving Data

In [17]:
datapath='../data'

save_file(users, 'users_cleaned.csv', datapath)

A file already exists with this name.

Do you want to overwrite? (Y/N)Y
Writing file.  "../data\users_cleaned.csv"


## 2.4. Movie ID Data 

### 2.4.1 General Data

In [18]:
movie_id.shape

(1682, 2)

In [19]:
movie_id.head()

item_id              title
0        1   Toy Story (1995)
1        2   GoldenEye (1995)
2        3  Four Rooms (1995)
3        4  Get Shorty (1995)
4        5     Copycat (1995)

### 2.4.2 Data Dictionary

In [20]:
report_movies=movie_id.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report_movies

### 2.4.3 Data Cleaning

#### 2.4.3.1 Checking Data Types

In [21]:
movie_id.dtypes

item_id     int64
title      object
dtype: object

In [22]:
# Converting item_id to string
movie_id['item_id']=movie_id['item_id'].astype(str)
movie_id.dtypes

item_id    object
title      object
dtype: object

#### 2.4.3.2 Checking Range Constraints

In [23]:
movie_id.describe()

item_id                  title
count     1682                   1682
unique    1682                   1664
top        190  Body Snatchers (1993)
freq         1                      2

#### 2.4.3.3 Checking for duplicates

In [24]:
# checking for duplicated movie titles
movie_id.duplicated(subset='title', keep='first').value_counts()

False    1664
True       18
dtype: int64

In [25]:
# dropped the 18 duplicates
movie_id.drop_duplicates(subset='title', keep='first', inplace=True)

Since each movie id is unique, each movie title should be unique; however, there were 18 duplicated titles, so the 18 duplicates were removed

#### 2.4.3.4 Checking for Missing Values

In [26]:
movie_id.isna().any()

item_id    False
title      False
dtype: bool

### 2.4.4 Saving Data

In [27]:
datapath='..\data'

save_file(movie_id, 'movie_id_cleaned.csv', datapath)

A file already exists with this name.

Do you want to overwrite? (Y/N)Y
Writing file.  "..\data\movie_id_cleaned.csv"


## 2.5 Credit Data

### 2.5.1 General Info

In [28]:
credits.head()

cast  \
0  [{'cast_id': 14, 'character': 'Woody (voice)',...   
1  [{'cast_id': 1, 'character': 'Alan Parrish', '...   
2  [{'cast_id': 2, 'character': 'Max Goldman', 'c...   
3  [{'cast_id': 1, 'character': "Savannah 'Vannah...   
4  [{'cast_id': 1, 'character': 'George Banks', '...   

                                                crew     id  
0  [{'credit_id': '52fe4284c3a36847f8024f49', 'de...    862  
1  [{'credit_id': '52fe44bfc3a36847f80a7cd1', 'de...   8844  
2  [{'credit_id': '52fe466a9251416c75077a89', 'de...  15602  
3  [{'credit_id': '52fe44779251416c91011acb', 'de...  31357  
4  [{'credit_id': '52fe44959251416c75039ed7', 'de...  11862

In [29]:
credits.shape

(45476, 3)

### 2.5.2 Data Dictionary

In [30]:
report_credits=credits.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report_credits

The credits data seems of limited importance, so at this stage, I won't continue to clean it.

## 2.6. Keyword Data

### 2.6.1 General Info

In [31]:
keywords.head()

id                                           keywords
0    862  [{'id': 931, 'name': 'jealousy'}, {'id': 4290,...
1   8844  [{'id': 10090, 'name': 'board game'}, {'id': 1...
2  15602  [{'id': 1495, 'name': 'fishing'}, {'id': 12392...
3  31357  [{'id': 818, 'name': 'based on novel'}, {'id':...
4  11862  [{'id': 1009, 'name': 'baby'}, {'id': 1599, 'n...

In [32]:
keywords.shape

(46419, 2)

In [33]:
keywords.loc[0,'keywords']

"[{'id': 931, 'name': 'jealousy'}, {'id': 4290, 'name': 'toy'}, {'id': 5202, 'name': 'boy'}, {'id': 6054, 'name': 'friendship'}, {'id': 9713, 'name': 'friends'}, {'id': 9823, 'name': 'rivalry'}, {'id': 165503, 'name': 'boy next door'}, {'id': 170722, 'name': 'new toy'}, {'id': 187065, 'name': 'toy comes to life'}]"

### 2.6.2 Data Dictionary

In [34]:
report_keywords=keywords.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report_keywords

### 2.6.3 Data Cleaning

#### 2.6.3.1 Check for Data Types

In [35]:
keywords.dtypes

id           int64
keywords    object
dtype: object

In [36]:
# convert id to string
keywords['id']=keywords['id'].astype(str)
keywords.dtypes

id          object
keywords    object
dtype: object

#### 2.6.3.2 Checking for duplicates

In [37]:
# checking for duplicated in the id column
keywords.duplicated(subset='id', keep='first').value_counts()

False    45432
True       987
dtype: int64

In [38]:
# drop duplicated id's
keywords.drop_duplicates(subset='id', keep='first', inplace=True)
keywords.duplicated(subset='id', keep='first').value_counts()

False    45432
dtype: int64

Id represtents a movie; therefore, there should only be one entry for each movie, so I dropped the 987 duplicated movie id's

In [39]:
# checking for duplicates in the keywords column
keywords.duplicated(subset='keywords', keep='first').value_counts()

False    25989
True     19443
dtype: int64

In [40]:
keywords['keywords'].value_counts()

[]                                                                                                                                                                                                                                                                                                                                                                                                  14340
[{'id': 187056, 'name': 'woman director'}]                                                                                                                                                                                                                                                                                                                                                           1281
[{'id': 10183, 'name': 'independent film'}]                                                                                                                                                                         

Approximatley 43% of the movies keywords are duplicates. This may suggest that the keywords can be used to determine which movies are similar. However, since the data in the keywords column is stored as a list of dictionaries, so the duplicated function may have issue with this. Keywords will need to be explored deeper.

#### 2.6.3.3 Checking for missing values

In [41]:
keywords.isna().any()

id          False
keywords    False
dtype: bool

### 2.6.4 Saving Data

In [42]:
datapath='..\data'

save_file(keywords, 'keywords_cleaned.csv', datapath)

A file already exists with this name.

Do you want to overwrite? (Y/N)Y
Writing file.  "..\data\keywords_cleaned.csv"


## 2.7. links

### 2.7.1 General Infor

In [43]:
links.head()

movieId  imdbId   tmdbId
0        1  114709    862.0
1        2  113497   8844.0
2        3  113228  15602.0
3        4  114885  31357.0
4        5  113041  11862.0

In [44]:
links.shape

(45843, 3)

### 2.7.2 Data Dictionary

In [45]:
report_links=links.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report_links

### 2.7.3 Data Cleaning

#### 2.7.3.1 Data Types

In [46]:
# checking the data types
links.dtypes

movieId      int64
imdbId       int64
tmdbId     float64
dtype: object

In [47]:
# converting the data types to strings
links['movieId']=links['movieId'].astype(str)
links['imdbId']=links['imdbId'].astype(str)
links['tmdbId']=links['tmdbId'].astype(str)
links.dtypes

movieId    object
imdbId     object
tmdbId     object
dtype: object

#### 2.7.3.2 Duplicates

In [48]:
# checking for duplicates in movie ID
links.duplicated(subset='movieId', keep='first').value_counts()

False    45843
dtype: int64

In [49]:
# checking for duplicates in in imdbId
links.duplicated(subset='imdbId', keep='first').value_counts()

False    45843
dtype: int64

In [50]:
# checking for duplicates in the movie database ID
links.duplicated(subset='tmdbId', keep='first').value_counts()

False    45595
True       248
dtype: int64

In [51]:
# Each movie should only have one move database id; therefore, the 248 duplicated tmdbId's will be dropped
links.drop_duplicates(subset='tmdbId', keep='first', inplace=True)
links.duplicated(subset='tmdbId', keep='first').value_counts()

False    45595
dtype: int64

#### 2.7.3.3 Missing Data

In [52]:
links.isna().any()

movieId    False
imdbId     False
tmdbId     False
dtype: bool

### 2.7.4 Saving Data

In [53]:
datapath='..\data'

save_file(links, 'links_cleaned.csv', datapath)

A file already exists with this name.

Do you want to overwrite? (Y/N)Y
Writing file.  "..\data\links_cleaned.csv"


## 2.8. Movies Metadata

### 2.8.1 General info

In [65]:
movies_metadata.head()

adult                              belongs_to_collection    budget  \
0  False  {'id': 10194, 'name': 'Toy Story Collection', ...  30000000   
1  False                                                NaN  65000000   
2  False  {'id': 119050, 'name': 'Grumpy Old Men Collect...         0   
3  False                                                NaN  16000000   
4  False  {'id': 96871, 'name': 'Father of the Bride Col...         0   

                                              genres  \
0  [{'id': 16, 'name': 'Animation'}, {'id': 35, '...   
1  [{'id': 12, 'name': 'Adventure'}, {'id': 14, '...   
2  [{'id': 10749, 'name': 'Romance'}, {'id': 35, ...   
3  [{'id': 35, 'name': 'Comedy'}, {'id': 18, 'nam...   
4                     [{'id': 35, 'name': 'Comedy'}]   

                               homepage     id    imdb_id original_language  \
0  http://toystory.disney.com/toy-story    862  tt0114709                en   
1                                   NaN   8844  tt0113497                en   
2                                   NaN  15602  tt0113228                en   
3                                   NaN  31357  tt0114885                en   
4                                   NaN  11862  tt0113041                en   

                original_title  \
0                    Toy Story   
1                      Jumanji   
2             Grumpier Old Men   
3            Waiting to Exhale   
4  Father of the Bride Part II   

                                            overview  ... release_date  \
0  Led by Woody, Andy's toys live happily in his ...  ...   1995-10-30   
1  When siblings Judy and Peter discover an encha...  ...   1995-12-15   
2  A family wedding reignites the ancient feud be...  ...   1995-12-22   
3  Cheated on, mistreated and stepped on, the wom...  ...   1995-12-22   
4  Just when George Banks has recovered from his ...  ...   1995-02-10   

       revenue runtime                                   spoken_languages  \
0  373554033.0    81.0           [{'iso_639_1': 'en', 'name': 'English'}]   
1  262797249.0   104.0  [{'iso_639_1': 'en', 'name': 'English'}, {'iso...   
2          0.0   101.0           [{'iso_639_1': 'en', 'name': 'English'}]   
3   81452156.0   127.0           [{'iso_639_1': 'en', 'name': 'English'}]   
4   76578911.0   106.0           [{'iso_639_1': 'en', 'name': 'English'}]   

     status                                            tagline  \
0  Released                                                NaN   
1  Released          Roll the dice and unleash the excitement!   
2  Released  Still Yelling. Still Fighting. Still Ready for...   
3  Released  Friends are the people who let you be yourself...   
4  Released  Just When His World Is Back To Normal... He's ...   

                         title  video vote_average vote_count  
0                    Toy Story  False          7.7     5415.0  
1                      Jumanji  False          6.9     2413.0  
2             Grumpier Old Men  False          6.5       92.0  
3            Waiting to Exhale  False          6.1       34.0  
4  Father of the Bride Part II  False          5.7      173.0  

[5 rows x 24 columns]

In [66]:
movies_metadata.shape

(45466, 24)

### 2.8.2 Data Dictionary

In [67]:
report_movies_metadata=movies_metadata.profile_report(sort='None', html={'style':{'full_width': True}}, progress_bar=False)
report_movies_metadata

Adult variable needs to be a boolean and has a membership constraint. Need to drop belongs to collection because it is missing 90% of the data. Budget needs to be converted to integer or float. Genres is a list of dictionary, which need to be converted to list of values and formated as a category. Homepage is missing 82% of the data, so the column may be dropped. Imdb is missing some values and it may have duplicates. Original language has some missing values that will need to be imputed. Original_title has some duplicates, which need to be investigated. Overview has some missing data. Popularity has an unsupported type, so it will be removed. poster has some missing values. Production_company is a list of dictionaries, which needs to be converted to a single item or a list. Production_countries has the same problem as production_companies. Release date has missing values and needs to be converted to date time. Revenue only has 6 missing values. Runtime has missing values and also has zero runtime which doesn't make sense. Spoken_languages has same issue as production_companies. Status has some missing values, and the majority are labeled released, so it may provide only a little value. Tagline is missing 55% of the data, so tagline will likely be dropped. Title has 6 missing values. Video is a boolean, so it doesn't provide much information; therefore, it will be dropped. Vote average is only missing 6 entries. Vote count is the same. 

### 2.8.3 Cleaning Data

#### 2.8.3.1 Dropping Columns

In [68]:
# dropping belongs_to_collection, homepage, popularity, tagline, and video
movies_metadata.drop(columns=['belongs_to_collection', "homepage", 'popularity', 'tagline', 'video'], inplace=True)


In [69]:
#making sure the columns were dropped
movies_metadata.columns

Index(['adult', 'budget', 'genres', 'id', 'imdb_id', 'original_language',
       'original_title', 'overview', 'poster_path', 'production_companies',
       'production_countries', 'release_date', 'revenue', 'runtime',
       'spoken_languages', 'status', 'title', 'vote_average', 'vote_count'],
      dtype='object')

#### 2.8.3.2 Data Type

In [70]:
# converting budget to a float or integer
movies_metadata['budget']=movies_metadata['budget'].astype(float)

ValueError: could not convert string to float: '/ff9qCepilowshEtG2GYWwzt2bs4.jpg'

In [83]:
# replace jpeg file with 0
movies_metadata['budget']=movies_metadata['budget'].apply(lambda row: re.sub(r".+\.jpg", "0", row))
movies_metadata['budget']=movies_metadata['budget'].astype(int)

In [84]:
# converting release_date to a date
movies_metadata['release_date']=pd.to_datetime(movies_metadata['release_date'], format='%Y-%m-%d', infer_datetime_format=True, errors='coerce')

# checking the data types
movies_metadata.dtypes

adult                           object
budget                           int32
genres                          object
id                              object
imdb_id                         object
original_language               object
original_title                  object
overview                        object
poster_path                     object
production_companies            object
production_countries            object
release_date            datetime64[ns]
revenue                        float64
runtime                        float64
spoken_languages                object
status                          object
title                           object
vote_average                   float64
vote_count                     float64
new_budget                      object
dtype: object

In [85]:
# convert adult to category
#movies_metadata['adult']=movies_metadata['adult'].astype(bool)

# convert genres to category
#movies_metadata['genres']=movies_metadata['genres'].astype('category')

# convert origina_language to category
movies_metadata['original_language']=movies_metadata['original_language'].astype('category')

# convert status to category
movies_metadata['status']=movies_metadata['status'].astype('category')

movies_metadata.dtypes

adult                           object
budget                           int32
genres                          object
id                              object
imdb_id                         object
original_language             category
original_title                  object
overview                        object
poster_path                     object
production_companies            object
production_countries            object
release_date            datetime64[ns]
revenue                        float64
runtime                        float64
spoken_languages                object
status                        category
title                           object
vote_average                   float64
vote_count                     float64
new_budget                      object
dtype: object

#### 2.8.3.3 Duplicates

In [86]:
# movie id must be unique. Checking for duplicated id numbers
movies_metadata.duplicated(subset='id',keep='first').value_counts()

False    45436
True        30
dtype: int64

In [87]:
# dropping duplicated id
movies_metadata.drop_duplicates(subset='id', keep='first', inplace=True)
movies_metadata.duplicated(subset='id', keep='first').value_counts()

False    45436
dtype: int64

In [88]:
# checking for duplicates in imdb_id
movies_metadata.duplicated(subset=['imdb_id'], keep='first').value_counts()

False    45418
True        18
dtype: int64

In [89]:
# dropping duplicates in imdb_id
movies_metadata.drop_duplicates(subset='imdb_id', keep='first', inplace=True)
movies_metadata.duplicated(subset='imdb_id', keep='first').value_counts()

False    45418
dtype: int64

In [90]:
# checking the number of entries
movies_metadata.shape

(45418, 20)

#### 2.8.3.4 Membership constraints

In [91]:
# replace the one value that is not True or false with nan.
movies_metadata.loc[19730, 'adult']=np.nan

# verifying the action worked
movies_metadata['adult'].isna().any()

True

In [92]:
# checkings type
type(movies_metadata['genres'][0])

str

In [93]:
# looking at the pattern
movies_metadata['genres'][0]

"[{'id': 16, 'name': 'Animation'}, {'id': 35, 'name': 'Comedy'}, {'id': 10751, 'name': 'Family'}]"

#### 2.8.3.5 Missing Values

In [94]:
# checking for missing values
movies_metadata.isna().sum()

adult                     1
budget                    0
genres                    0
id                        0
imdb_id                   1
original_language        11
original_title            0
overview                952
poster_path             381
production_companies      3
production_countries      3
release_date             85
revenue                   4
runtime                 259
spoken_languages          4
status                   85
title                     4
vote_average              4
vote_count                4
new_budget                0
dtype: int64

### 2.8.4 Saving Data

In [95]:
datapath='..\data'

save_file(movies_metadata, 'movies_metadata_cleaned.csv', datapath)

A file already exists with this name.

Do you want to overwrite? (Y/N)Y
Writing file.  "..\data\movies_metadata_cleaned.csv"


## 2.9. Rating Data

### 2.9.1 General Info

In [96]:
ratings.head()

userId  movieId  rating   timestamp
0       1      110     1.0  1425941529
1       1      147     4.5  1425942435
2       1      858     5.0  1425941523
3       1     1221     5.0  1425941546
4       1     1246     5.0  1425941556

In [97]:
ratings.shape

(26024289, 4)

### 2.9.2 Data Dictionary

In [98]:
ratings.describe()

userId       movieId        rating     timestamp
count  2.602429e+07  2.602429e+07  2.602429e+07  2.602429e+07
mean   1.350371e+05  1.584911e+04  3.528090e+00  1.171258e+09
std    7.817620e+04  3.108526e+04  1.065443e+00  2.052889e+08
min    1.000000e+00  1.000000e+00  5.000000e-01  7.896520e+08
25%    6.716400e+04  1.073000e+03  3.000000e+00  9.907545e+08
50%    1.351630e+05  2.583000e+03  3.500000e+00  1.151716e+09
75%    2.026930e+05  6.503000e+03  4.000000e+00  1.357578e+09
max    2.708960e+05  1.762750e+05  5.000000e+00  1.501830e+09

In [99]:
# checking for missing data
ratings.isna().any()

userId       False
movieId      False
rating       False
timestamp    False
dtype: bool

In [100]:
# checking data types
ratings.dtypes

userId         int64
movieId        int64
rating       float64
timestamp      int64
dtype: object

### 2.9.3 Cleaning Data

#### 2.9.3.1 Dropping Column

In [101]:
# dropping the timestamp column
ratings.drop(columns='timestamp', axis=0, inplace=True)

#verifying column names
ratings.columns

Index(['userId', 'movieId', 'rating'], dtype='object')

#### 2.9.3.2. Data types

In [102]:
# converting userId and movieId to strings
ratings['userId']=ratings['userId'].astype(str)
ratings['movieId']=ratings['movieId'].astype(str)

# verifying data types
ratings.dtypes

userId      object
movieId     object
rating     float64
dtype: object

### 2.9.4 Saving Data

In [67]:
datapath='..\data'

save_file(ratings, 'ratings.cleaned.csv', datapath)

Writing file.  "..\data\ratings.cleaned.csv"


For movies_metadata: Need to change genres, production_companies, and production_countries to list; however, the data is saved as string. Thus, I need to learn how to use regular expression to do this.

May have to scrape the internet to fill in the missing adult value, imdb_id, original_title, overview, production_company, production_countries, release_date, runtime, spoken_languages, status, title. The poster_path can likely be dropped. Revenue, vote_average, and vote_count can likely be imputed using the median value.  